## 作业三：爬取教授信息并结构化处理

## <操作步骤>

第一步：导入需要用到的模块

In [14]:
import re
import requests
import pandas
import pandas as pd

第二步：将老师姓名与对应简历网页联结

In [15]:
url1 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-1.html" 
url2 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-2.html"

def get_teachers_href(url):
    r=requests.get(url)
    html_text=r.text
    searchObj_s=re.findall(r'<div class="textlist">.*?</div>',html_text)
    links_teacher={}
    for item in searchObj_s:
        name = item[81:-10]
        name=name.replace(' ','')
        href = item[32:79]
        links_teacher[name]=href
    return(links_teacher)
    
links1=get_teachers_href(url1)
links2=get_teachers_href(url2)
links = dict(links1,**links2)
links = dict(links1,**links2)
herfs = list(links.values())

第三步：为爬取结构化数据定义一个模板

In [16]:
def get_value(key,html):
    pattern='%s</strong>.*?：(.*?)</p>' % key
    searchObj=re.search(pattern,html)
    value=searchObj.group(1)
    return(value)

def get_zwjj(key,html):
    self_intro = re.findall(r'自我简介(.*?)科研成果', html)
    self_intro_text = re.sub(r'</p>','\n',self_intro[0])
    self_intro_text_clear = re.sub(r'<(.*?)>','', self_intro_text).replace("&nbsp;","").replace("\n"," ").strip()
    return self_intro_text_clear

def get_kycg(ley,html):
    sci = re.findall(r'<span>科研成果(.*?)版权所有',html,re.S)
    sci_text = re.sub(r'</p>','\n',sci[0])
    sci_text_clear = re.sub(r'<(.*?)>','', sci_text).replace("&nbsp;","").replace("\n"," ").strip("：").strip()
    return sci_text_clear
    

def parse_content(html):
    xm = get_value('姓　　名',html)
    xb = get_value('性　　别',html)
    csny = get_value('出生年月',html)
    zzmm = get_value('政治面貌',html)
    byyx = get_value('毕业院校',html)
    byzy = get_value('毕业专业',html)
    zw = get_value('职　　务',html)
    zc = get_value('职　　称',html)
    yx = get_value('邮&nbsp; &nbsp; &nbsp; &nbsp;箱',html)
    zwjj = get_zwjj('自我简介',html)
    kycg = get_kycg('科研成果',html)
    teacher_into = {'姓名':xm,
                    '性别':xb,
                    '出生年月':csny,
                    '政治面貌':zzmm,
                    '毕业院校':byyx,
                    '毕业专业':byzy,
                    '职务':zw,
                    '职称':zc,
                    '邮箱':yx,
                    '自我简介':zwjj,
                    '科研成果':kycg
                               }
    return(teacher_into)

第四步：将不符合模板要求的教授信息剔除

In [17]:
tol_list = []
def fail_list(herfs):
    fail_list = []
    for i in range(len(herfs)):
        t = requests.get(herfs[i]).text
        try:
            parse_content(t)
            a = parse_content(t)
            tol_list.append(a)
        except:
           fail_list.append(i)
    return fail_list 
fail_list(herfs)

[3, 4, 5, 8, 9, 10, 14, 17]

第五步：信息整合结果呈现

In [18]:
tol_list

[{'姓名': '曹邓',
  '性别': '女',
  '出生年月': '',
  '政治面貌': '中共党员',
  '毕业院校': '江西财经大学',
  '毕业专业': '管理学',
  '职务': '系副主任',
  '职称': '教授',
  '邮箱': 'laotoutou@aliyun.com',
  '自我简介': '一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险理论与创新 二、获得奖励：1996年获江西财经大学优秀工作者称号；2001年获江西财经大学优秀班主任称号；2003年、2010年获江西财经大学先进工作 者称号；2003年被评为江西财经大学金融学院优秀教师二等奖，2004年获江西省高校优秀班主任称号。2006年获江西省师德师风标兵称号 三、社会兼职：中国保险学会会员、江西保险学会会员',
  '科研成果': '一、论文 1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。 2.“保险费率的构成及其厘定”，独著，《江西财经大学学报》2000年第1期。 3.“如何评价高新技术企业价值”，独著，《澳港信息日报》（中国投资）2002年5月15日。 4.“加强财政监管，促进社会保障税费改革”，独著，《时策聚焦》2002年1月。 5.“开征社会保障税，摆脱养老保险基金筹资困境”，独著，《探索与创新》2002年8月”。 6.“经济全球化背景下的就业环境、就业结构与就业保障”，独著，《社会保障问题研究》2003年9月。 7.“我国保险资金运用与债券市场发展问题探讨”，独著，《未来与发展》2004年第4期。 8.“论我国保险信用体系的建设”，独著，《未来与发展》2004年第6期。 9.“我国保险资金运用与债券市场发展问题探讨”，独著，《未来与发展》2004年第4期。 10.“我国存款保险制度运行模式的构想”，独著，《价格月刊》2004年第10期。 11.“保险诚信问题分析与保险诚信体系建设”，独著，《金融与经济》2005年第11期。 12.“可持续发展思想的演变与诠释》‘独著，《当代财经》2005年第11期。 13.“《论我国农户小额信贷需求的层次性》，第一作者，《价格月刊》2007第八期。 14.“对我国财产保险创新及创新路径之若干问题的思考”独著，《价格月刊》2008年第12期。 

第六步：将爬取的数据可视化（字典列表转Pandas DataFrame）

In [22]:
pd.DataFrame.from_dict(tol_list)
df =  pd.DataFrame.from_dict(tol_list)
order = ['姓名','性别','出生年月','政治面貌','毕业院校','毕业专业','职务','职称','邮箱','自我简介','科研成果']
df = df[order]

In [23]:
df

姓名 性别 出生年月  政治面貌    毕业院校  \
0                                                 曹邓  女       中共党员  江西财经大学   
1                                                陈春霞  女         群众  江西财经大学   
2                                                陈家洪  男       中共党员  江西财经大学   
3  吕江林<img style="float:right;padding-left:10px;"...  男       中共党员  中南财经大学   
4                                                刘兴华  男       中共党员    厦门大学   
5                                                孙爱琳  女       中共党员    浙江大学   
6                                          王 &nbsp;辉          中共党员  江西财经大学   
7                                                 汪洋  男       中共党员  上海财经大学   
8                                                杨玉凤  女       民主党派  江西财经大学   
9                                                 杨荣  女       中共党员  江西财经大学   

           毕业专业          职务     职称  \
0           管理学        系副主任     教授   
1           金融学              教授/硕导   
2  经济统计（证券研究方向）              教授/硕导   
3           经济学  应用金融研究中心主任  教授/博导   
4          世界经济         副院长  教授/博导   
5         政治经济学              教授、硕导   
6           财政学              教授/硕导   
7           金融学              教授/博导   
8           金融学              教授/硕导   
9           金融学              教授、硕导   

                                                  邮箱  \
0                               laotoutou@aliyun.com   
1                                    new9360@163.com   
2                                     jxmcjh@126.com   
3                                    ljl5983@126.com   
4                                    lxh7572@126.com   
5                                    sal6660@126.com   
6  “保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学”；“风险管理”；“证...   
7                              wangyang@jxufe.edu.cn   
8                                  xialuoren@126.com   
9                               yonghongyang@163.com   

                                                自我简介  \
0  一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险...   
1  开设课程 本科生主讲的主要课程有：《货币银行学》、《国际金融》《金融企业会计》、《投资项目评...   
2      一、开设课程：证券投资学、证券投资基金、投资管理、创业投资管理、私募股权投资、证券投资分析   
3  一、开设课程本科生课程:货币银行学、国际金融、证券投资学、商业银行经营管理学、金融工程硕士生...   
4  一、开设课程 系统讲授《国际金融》、《国际货币与金融经济学》、《货币银行学》、《中央银行学》...   
5  一、开设课程 本科生：货币银行学、财政学、预算会计、保险学、保险会计、社会保障学等。 研究生...   
6  一、开设课程 本科生：“保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学...   
7  一、开设课程：本科：《国际金融》，《国际货币与金融经济学》，《中央银行学》；硕士研究生：《国...   
8  一、开设课程  主要有《国际金融》、《国际金融实务》、《货币银行学》等课程。 二、获得奖励 ...   
9    一、开设课程：货币银行学、商业银行学、 二、获得奖励：略 三、社会兼职：江西省货币学会常务理事   

                                                科研成果  
0  一、论文 1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。 ...  
1  一、论文 1、《我国国债与企业债券的比较》，独著，《江西财经大学学报》2006年第9月期（人...  
2  一、论文1. “从股票市场角度看收入分配不公问题”，独著，《华东经济管理》2011年第8期。...  
3  主要科研成果一、论文1、《具有联合椭圆不确定集与概率约束的鲁棒投资组合选择》，《控制与决策》...  
4  一、论文 1.“日本银行对日元汇率的干预：基于动态博弈的分析”，第一作者，《现代日本经济》2...  
5  一、论文 1.“完善我国国家公务员养老保险制度的思考”，独著，《江西财经大学学报》2001年...  
6  一、论文 1.“加快建立有中国特色的社会保障法律体系”，独著，《财经论丛》2000年第3期。...  
7  发表的主要论文：1. 《跨境贸易以人民币结算：路径选择与风险》，《国际经济评论》，独著，20...  
8  一、论文 1.“加快表外业务的发展和创新”，独著，《金融与经济》2002年第3期。 2.“从...  
9  一、论文 2000年以来论文 1、影响我国企业集团形成与健康发展原因剖析 《国民经济运行与调...

### <作业心得>

   本次作业还存在一些不足之处，如：爬取教授信息定义的模板不够完善，以至于匹配失效的教授数目很多（共需爬取18位教授的信息，其中成功爬取10位教授的信息，8位教授信息爬取失败），爬取信息不完全。还有就是正则表达式使用还不够灵活，爬取的信息中有个别出错，如邮箱爬取错误。这些是以后值得改进的地方。
   通过这份作业，我感觉自己不仅操作更加熟练，而且也更加锻炼了自己遇到问题积极解决的心境。因为在做作业时总会出现各种各样的报错，从茫然无措、不知如何下手到慢慢找到感觉，自己上网百度，询问同学、老师，现在也可以解决一些小问题了。万事开头难，而且编程的门槛我觉得更高，因为一开始根本就不熟悉，感觉无数次想放弃，无数次怀疑自己，怎么就这么差，编程都学不会。但当自己在电脑前慢慢摸索，到后来也能敲出一些有逻辑的代码出来时，我感觉到了很大的满足，即使只是一个非常微小的进步。并且很不可思议的是我发现有时候怎么都转不过来的一个弯，原来就差那么几步，就只是被几行小代码给挡住，所以我更加觉得敲代码就像一场修行，无比锻炼人的意志和能力。这次作业对我来说更像是开启爬数据之旅的钥匙，既让我窥见了门后数据处理的广阔天地，也让我对数据处理的过程产生敬畏！